# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [20 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 431, done.
remote: Counting objects: 100% (38/38), done.
remote: Compressing objects: 100% (33/33), done.
remote: Total 431 (delta 10), reused 26 (delta 4), pack-reused 393
Receiving objects: 100% (431/431), 175.94 MiB | 22.09 MiB/s, done.
Resolving deltas: 100% (159/159), done.
Checking out files: 100% (215/215), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          RL_VPP_Thesis/
Algorithm_simulator_notebooks/    trained_models/
data/                             VPP_environment.py
EV_experiment_notebooks/          VPP_simulator.ipynb
Hyperparameters_sweep_notebooks/  wandb/
README.md


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f1b236c6450>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  20811.12 , over-consume=kWh  38241.87 , under-consume=kWh  17430.75 , Total_cost=€  868.19 , overcost=€  1374.45 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21519.89 , over-consume=kWh  38751.18 , under-consume=kWh  17231.29 , Total_cost=€  833.11 , overcost=€  1339.25 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3627.09 , over-consume=KWh  2125.21 , under-consume=KWh  5752.3 , Total_cost=€  -85.03 , Overcost=€  74.12 
 EV_INFO: Av.EV_energy_leaving=kWh  66.77 , Std.EV_energy_leaving=kWh  23.97 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 406019.78 - Step_rewars (load_t= 368192.34, EVs_energy_t= 15523.95)
 - Final_rewards (EVs_energy= 16750.48, Overconsume= -1422.14, Underconsume= -2509.29, Overcost= 9484.43)
Episode:1 Score:406019.7838054474


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0    1          2          3  \
time                                                        
2022-01-01 00:00:00  57.479755  0.0  36.228638  36.361340   
2022-01-01 00:15:00  57.479755  0.0  36.478638  35.505135   
2022-01-01 00:30:00  57.479755  0.0  36.728638  34.827618   
2022-01-01 00:45:00  57.479755  0.0  36.978638  34.078068   
2022-01-01 01:00:00  57.479755  0.0  37.228638  33.552559   
...                        ...  ...        ...        ...   
2022-06-06 04:45:00  75.240578  0.0  70.591377  68.969620   
2022-06-06 05:00:00  75.240578  0.0  72.050087  70.428329   
2022-06-06 05:15:00  75.240578  0.0  73.643616  72.021858   
2022-06-06 05:30:00  75.240578  0.0  75.156715  73.534958   
2022-06-06 05:45:00  75.240578  0.0  76.664192  75.042435   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [0, 2, 1, 2]   
2022-01-01 00:15:00  [3128, 0, 3127, 3129]  [0, 2, 1, 2]   
2022-01-01 00:30:00  [3128, 0, 3127, 3129]  [0, 2, 1, 2]   
2022-01-01 00:45:00  [3128, 0, 3127, 3129]  [0, 2, 1, 2]   
2022-01-01 01:00:00  [3128, 0, 3127, 3129]  [0, 2, 1, 2]   
...                                    ...           ...   
2022-06-06 04:45:00  [3568, 0, 3570, 3569]  [0, 2, 1, 1]   
2022-06-06 05:00:00  [3568, 0, 3570, 3569]  [0, 2, 1, 1]   
2022-06-06 05:15:00  [3568, 0, 3570, 3569]  [0, 2, 1, 1]   
2022-06-06 05:30:00  [3568, 0, 3570, 3569]  [0, 2, 1, 1]   
2022-06-06 05:45:00  [3568, 0, 3570, 3569]  [0, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [True, False, False, False]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        1.000000   
2022-01-01 00:30:00  [False, False, False, True]        1.000000   
2022-01-01 00:45:00  [False, False, False, True]        1.000000   
2022-01-01 01:00:00  [False, False, False, True]        1.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]        9.671257   
2022-06-06 05:00:00    [True, False, True, True]       11.669673   
2022-06-06 05:15:00    [True, False, True, True]       12.748255   
2022-06-06 05:30:00    [True, False, True, True]       12.104779   
2022-06-06 05:45:00    [True, False, True, True]       12.059816   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00           0.000000  1.652489e+00         15.0        0.0   
2022-01-01 00:15:00          -3.424823  0.000000e+00         15.0        0.0   
2022-01-01 00:30:00          -2.710071 -2.220446e-16         15.0        0.0   
2022-01-01 00:45:00          -2.998205  0.000000e+00         15.0        0.0   
2022-01-01 01:00:00          -2.102037  0.000000e+00         15.0        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00          -1.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:00:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:15:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:30:00           0.000000  0.000000e+00         15.0        0.0   
2022-06-06 05:45:00           0.000000  0.000000e+00         15.0        0.0   

                     rewards  
time                          
2022-01-01 00:00:00     15.0  
2022-01-01 00:15:00     15.0  
2022-01-01 00:30:00     15.0  
2022-01-01 00:45:00     15.0  
2022-01-01 01:00:00     15.0  
...                      ...  
2022-06-06 04:45:00     15.0  
2022-06-06 05:00:00     15.0  
2022-06-06 05:15:00     15.0  
2022-06-06 05:30:00     15.0  
2022-06-06 05:45:00     15.0  

[15000 rows x 13 columns]

In [25]:
#env.plot_Elvis_results()

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_Elvis_comparison()

In [29]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [30]:
env.plot_rewards_stats()

In [31]:
env.plot_EVs_kpi()

In [32]:
env.plot_load_kpi()

In [33]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [34]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 09:30:00, Parking_time: 21.362956232514296, Leaving_time: 2022-01-02 06:51:46.642437, SOC: 0.6138274117261922, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 22:00:00, Parking_time: 22.448006632131012, Leaving_time: 2023-01-01 20:26:52.823876, SOC: 0.32563902140554624, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13089.66 , over-consume=kWh  35044.2 , under-consume=kWh  21954.54 , Total_cost=€  630.04 , overcost=€  1532.4 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [35]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [36]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [37]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13104.46 , over-consume=kWh  34474.15 , under-consume=kWh  21369.69 , Total_cost=€  638.82 , overcost=€  1505.02 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7333.62 , over-consume=KWh  1142.04 , under-consume=KWh  8475.66 , Total_cost=€  -287.46 , Overcost=€  48.27 
 EV_INFO: Av.EV_energy_leaving=kWh  71.55 , Std.EV_energy_leaving=kWh  23.44 , EV_departures =  1040 , EV_queue_left =  0
SCORE:  Cumulative_reward= 405640.97 - Step_rewars (load_t= 348310.45, EVs_energy_t= 29742.09)
 - Final_rewards (EVs_energy= 17904.54, Overconsume= -535.82, Underconsume= -3686.64, Overcost= 13906.34)
Episode:1 Score:405640.9662851535


In [38]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [39]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  59.477673  33.728832  52.474411  84.316612   
2022-06-06 05:00:00  60.715893  33.478832  53.712631  85.554832   
2022-06-06 05:15:00  61.936859  33.228832  54.933598  86.775803   
2022-06-06 05:30:00  63.225487  32.978832  56.222225  88.064430   
2022-06-06 05:45:00  64.554657  32.728832  57.551399  89.393600   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [6704, 6703, 6705, 6702]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [6704, 6703, 6705, 6702]  [1, 2, 1, 1]   
2022-06-06 05:15:00  [6704, 6703, 6705, 6702]  [1, 2, 1, 1]   
2022-06-06 05:30:00  [6704, 6703, 6705, 6702]  [1, 2, 1, 1]   
2022-06-06 05:45:00  [6704, 6703, 6705, 6702]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]       11.720842   
2022-06-06 05:00:00    [True, False, True, True]       14.858625   
2022-06-06 05:15:00    [True, False, True, True]       14.651602   
2022-06-06 05:30:00    [True, False, True, True]       15.463543   
2022-06-06 05:45:00    [True, False, True, True]       15.950081   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.762379e+00    -4.692020        0.0   
2022-01-01 00:15:00                0.0 -3.815212e+00    -5.164241        0.0   
2022-01-01 00:30:00                0.0 -4.180665e+00    -3.919252        0.0   
2022-01-01 00:45:00                0.0 -3.351551e+00    -4.604995        0.0   
2022-01-01 01:00:00                0.0 -3.762997e+00    -4.204701        0.0   
...                                ...           ...          ...        ...   
2022-06-06 04:45:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:00:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:15:00               -1.0 -1.776357e-15    15.000000        0.0   
2022-06-06 05:30:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 05:45:00               -1.0  0.000000e+00    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.692020  
2022-01-01 00:15:00  -5.164241  
2022-01-01 00:30:00  -3.919252  
2022-01-01 00:45:00  -4.604995  
2022-01-01 01:00:00  -4.204701  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:4

In [40]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [41]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_Elvis_comparison()

In [43]:
env.plot_rewards_results()

In [44]:
env.plot_rewards_stats()

In [45]:
env.plot_EVs_kpi()

In [46]:
env.plot_load_kpi()

In [47]:
env.plot_yearly_load_log()

## Training dataset VPP Simulation using the loaded trained model

In [48]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-01 10:00:00, Parking_time: 23.393542831918275, Leaving_time: 2022-01-02 09:23:36.754195, SOC: 0.595030368260678, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 23:30:00, Parking_time: 23.799721978049103, Leaving_time: 2023-01-01 23:17:58.999121, SOC: 0.30818893589159946, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8775.64 , over-consume=kWh  32271.38 , under-consume=kWh  23495.73 , Total_cost=€  471.3 , overcost=€  1342.6 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [49]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

In [50]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [51]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  7920.27 , over-consume=kWh  31471.12 , under-consume=kWh  23550.85 , Total_cost=€  436.95 , overcost=€  1306.43 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -9017.71 , over-consume=KWh  1297.69 , under-consume=KWh  10315.4 , Total_cost=€  -303.15 , Overcost=€  52.42 
 EV_INFO: Av.EV_energy_leaving=kWh  74.37 , Std.EV_energy_leaving=kWh  22.39 , EV_departures =  1041 , EV_queue_left =  0
SCORE:  Cumulative_reward= 387164.83 - Step_rewars (load_t= 322795.77, EVs_energy_t= 38818.38)
 - Final_rewards (EVs_energy= 18503.67, Overconsume= -866.71, Underconsume= -4462.6, Overcost= 12376.31)
Episode:1 Score:387164.8256188947


In [52]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  98.997665  46.852383  73.422691  77.722778   
2022-06-06 03:45:00  99.414223  46.602383  73.839249  78.139336   
2022-06-06 04:00:00  99.989998  46.352383  74.450714  78.750801   
2022-06-06 04:15:00  99.989998  46.102383  75.061234  79.361320   
2022-06-06 04:30:00  99.989998  45.852383  75.728935  80.029022   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 03:30:00  [9848, 9849, 9847, 9850]  [1, 2, 1, 1]   
2022-06-06 03:45:00  [9848, 9849, 9847, 9850]  [1, 2, 1, 1]   
2022-06-06 04:00:00  [9848, 9849, 9847, 9850]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [9848, 9849, 9847, 9850]  [1, 2, 1, 1]   
2022-06-06 04:30:00  [9848, 9849, 9847, 9850]  [1, 2, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00   [False, False, True, True]        5.177900   
2022-06-06 03:45:00   [False, False, True, True]        4.998691   
2022-06-06 04:00:00   [False, False, True, True]        7.194858   
2022-06-06 04:15:00   [False, False, True, True]        4.884165   
2022-06-06 04:30:00   [False, False, True, True]        5.341650   

                     ev_discharged_pwr          load  load_reward  EV_reward  \
time                                                                           
2022-01-01 00:00:00                0.0 -3.529545e+00    -5.356118        0.0   
2022-01-01 00:15:00                0.0 -4.391730e+00    -4.466383        0.0   
2022-01-01 00:30:00                0.0 -3.679830e+00    -4.300721        0.0   
2022-01-01 00:45:00                0.0 -3.580433e+00    -5.216526        0.0   
2022-01-01 01:00:00                0.0 -4.238179e+00    -6.170115        0.0   
...                                ...           ...          ...        ...   
2022-06-06 03:30:00               -1.0  0.000000e+00    15.000000        0.0   
2022-06-06 03:45:00               -1.0  4.440892e-16    12.858524        0.0   
2022-06-06 04:00:00               -1.0 -1.427651e-01    -2.403449        0.0   
2022-06-06 04:15:00               -1.0 -2.442070e+00    -2.784687        0.0   
2022-06-06 04:30:00               -1.0 -2.670812e+00    -2.490124        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -5.356118  
2022-01-01 00:15:00  -4.466383  
2022-01-01 00:30:00  -4.300721  
2022-01-01 00:45:00  -5.216526  
2022-01-01 01:00:00  -6.170115  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  12.858524  
2022-06-06 04:00:00  -2.403449  
2022-06-06 04:15:00  -2.784687  
2022-06-06 04:3

In [54]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_Elvis_comparison()

In [57]:
env.plot_rewards_results()

In [58]:
env.plot_rewards_stats()

In [59]:
env.plot_EVs_kpi()

In [60]:
env.plot_actions_kpi()

In [61]:
env.plot_load_kpi()

In [62]:
env.plot_yearly_load_log()

In [63]:
#env.close()